In [1]:
import plotly
import plotly.express as px
import plotly.graph_objects as go
from skimage import data, filters, measure, morphology
import cv2
from tkinter import Tk
from tkinter.filedialog import askopenfilename

In [3]:
import tkinter as tk
import tkinter.filedialog as fd

root = tk.Tk()
files = fd.askopenfilenames(parent=root, title="Choose mircostructure images")

In [4]:
#get file names
pic_names = []
for i in range(len(files)):
    pic_name = files[i].split('/')[-1].split('.')[-2]
    pic_names.append(pic_name)

In [5]:
pic_names

['1', 'low_C']

In [8]:
for file in files:
    img = cv2.imread(file,0)
    # Gray scale picture
    threshold = filters.threshold_otsu(img)
    mask = img > threshold
    # Remove small object - carbon
    mask = morphology.remove_small_objects(mask, 1)
    mask = morphology.remove_small_holes(mask, 1)
    label_img = measure.label(mask) #labelling images

    fig = px.imshow(img, binary_string=True)
    fig.update_traces(hoverinfo= 'skip')  #hover info for label images only
    #init for properties : area
    props = measure.regionprops(label_img)
    properties = ['area']

    # For each label, add a filled scatter trace for its contour, display area of the label in the hover of this trace
    for index in range(0, label_img.max()):
        label_i = props[index]['label']
        contour = measure.find_contours(label_img == label_i, 0.5)[0]
        y, x = contour.T
        hoverinfo = ''
        for prop_name in properties:
            hoverinfo += f'<b> {label_i}-{prop_name}: {getattr(props[index], prop_name):.2f} </b><br>'
            fig.add_trace(go.Scatter( 
                x=x, y=y, name=label_i,
                mode = 'lines', fill='toself', showlegend=True,
                hovertemplate= hoverinfo, hoveron='points+fills'
                ))
    plotly.io.show(fig)
    
    #collect grain size data
    grain_size = []
    for i in range(0, label_img.max()):
        grain_size_i = props[i]['area_filled']
        grain_size.append(grain_size_i)


In [9]:
#create DataFrame of grain size collected above
list_of_tuple = list(zip(pic_names, grain_size))
list_of_tuple

[('1', 150140.0), ('low_C', 7.0)]

In [10]:
import pandas as pd

df = pd.DataFrame(list_of_tuple, columns=['Pic_name','Grain_size_ave'])
df

Pic_name  Grain_size_ave
0        1        150140.0
1    low_C             7.0

In [ ]:
df.to_csv('Grain_size_pixel_units.csv')